In [ ]:
# label transfer with Symphony?

In [2]:
library(symphony)
library(Seurat)
library(dplyr)
library(ggplot2)
library(SingleCellExperiment)
library(irlba)

In [3]:
# load reference
heart.ref = readRDS('~/septation/markers/Qiu_E9.5_seuratObj.rds')
ls()
heart.ref <- NormalizeData(heart.ref)  # default normalization - 1e4 scaling

[1] "heart.ref"

Normalizing layer: counts



In [4]:
ref_exp_full = heart.ref@assays$RNA@layers$data
rownames(ref_exp_full) = rownames(heart.ref)
colnames(ref_exp_full) = rownames(heart.ref@meta.data)
ref_metadata = heart.ref@meta.data

In [8]:
# HVGs - 10k for E9.5, E10.5, E11.5 - to have enough genes after subsetting to 1-1 orthologs
var_genes = vargenes_vst(ref_exp_full, groups = as.character(ref_metadata[['sample']]), topn = 5000)
ref_exp = ref_exp_full[var_genes, ]
dim(ref_exp)

[1]  10543 336999

In [6]:
vargenes_means_sds = tibble(symbol = var_genes, mean = Matrix::rowMeans(ref_exp))
vargenes_means_sds$stddev = singlecellmethods::rowSDs(ref_exp, vargenes_means_sds$mean)
head(vargenes_means_sds)

symbol        mean         stddev     
1 Dcc           1.326959e+00 1.709991874
2 Olfr1291-ps1  5.486794e-05 0.010282784
3 Slc4a1        1.693945e-01 0.756197209
4 Igkv3-7       9.621993e-06 0.005585722
5 Olfr820       3.322521e-05 0.008060284
6 4932429P05Rik 1.347884e-05 0.005970343

In [ ]:
ref_exp_scaled = singlecellmethods::scaleDataWithStats(ref_exp, vargenes_means_sds$mean,
                                                       vargenes_means_sds$stddev, 1)

In [19]:
set.seed(0)
s = irlba(ref_exp_scaled, nv = 20)
Z_pca_ref = diag(s$d) %*% t(s$v) # [pcs by cells]
loadings = s$u

In [20]:
unique(ref_metadata$sample)

[1] "embryo_38"

In [21]:
# add fake exp id to increase no. of samples for harmony-integration
ref_metadata$sample[sample(1:dim(ref_metadata)[1], 115000, replace = F)] = 'embryo_38_fake'

In [22]:
set.seed(0)
ref_harmObj = harmony::HarmonyMatrix(
        data_mat = t(Z_pca_ref),  ## PCA embedding matrix of cells
        meta_data = ref_metadata, ## dataframe with cell labels
        theta = c(2),             ## cluster diversity enforcement
        vars_use = c('sample'),    ## variable to integrate out
        nclust = 100,             ## number of clusters in Harmony model
        max.iter.harmony = 20,
        return_object = TRUE,     ## return the full Harmony model object
        do_pca = FALSE            ## don't recompute PCs
)

Warning message:
“HarmonyMatrix is deprecated and will be removed in the future from the API in the future”
Transposing data matrix

Initializing state using k-means centroids initialization

Warning message:
“Quick-TRANSfer stage steps exceeded maximum (= 11692150)”
Warning message:
“Quick-TRANSfer stage steps exceeded maximum (= 11692150)”
Warning message:
“Quick-TRANSfer stage steps exceeded maximum (= 11692150)”
Warning message:
“Quick-TRANSfer stage steps exceeded maximum (= 11692150)”
Warning message:
“Quick-TRANSfer stage steps exceeded maximum (= 11692150)”
Harmony 1/10

Harmony 2/10

Harmony converged after 2 iterations



In [23]:
# Compress a Harmony object into a Symphony reference
reference = symphony::buildReferenceFromHarmonyObj(
                           ref_harmObj,            # output object from HarmonyMatrix()
                           ref_metadata,           # reference cell metadata
                           vargenes_means_sds,     # gene names, means, and std devs for scaling
                           loadings,               # genes x PCs matrix
                           verbose = TRUE,         # verbose output
                           do_umap = FALSE)

Save metadata, vargenes (S), and loadings (U)

Save R, Z_orig, Z_corr, and betas from Harmony object

Calculate final L2 normalized reference centroids (Y_cos)

Calculate reference compression terms (Nr and C)

Finished nicely.



In [24]:
saveRDS(reference, 'Qiu_E11.5_harmonyObj.rds')